In [ ]:
import json
import csv
from typing import List, Dict, Any

def ensemble_best_answers(json_data_list: List[Dict[str, Any]], output_csv_path: str):
    """
    여러 JSON 파일에서 각 문제 ID별로 가장 높은 확률의 답변을 추출하여 CSV로 저장합니다.

    Args:
        json_data_list: 여러 JSON 파일에서 로드된 데이터 (딕셔너리 리스트).
        output_csv_path: 최종 CSV 파일을 저장할 경로.
    """
    
    # { 문제 ID: (최대 확률, 답변 텍스트) }를 저장할 딕셔너리
    best_answers: Dict[str, tuple[float, str]] = {}

    for data in json_data_list:
        # JSON 파일 내의 모든 문제 ID를 순회
        for q_id, predictions in data.items():
            
            # 현재 문제 ID에 대한 답변 후보들 중 가장 높은 확률을 찾음
            if not predictions:
                continue

            best_prediction_in_file = predictions[0]  # 가장 높은 확률
            current_prob = best_prediction_in_file['probability']
            current_text = best_prediction_in_file['text']

            # 현재까지 저장된 최상위 확률과 비교
            if q_id not in best_answers or current_prob > best_answers[q_id][0]:
                # 새로운 최상위 확률/답변을 업데이트
                best_answers[q_id] = (current_prob, current_text)

    # CSV 파일로 저장
    with open(output_csv_path, 'w', newline='', encoding='utf-8') as csvfile:
        writer = csv.writer(csvfile, delimiter='\t')
        
        for q_id, (prob, text) in best_answers.items():
            writer.writerow([q_id, text])
            
    print(f"앙상블 결과가 '{output_csv_path}'에 저장되었습니다. (총 {len(best_answers)}개 문제)")



json_file_paths = [
    '/data/ephemeral/home/roberta/outputs/korquad_2e5_kiwi_hybrid/nbest_predictions.json',
    '/data/ephemeral/home/roberta/outputs/korquad_2e5_ner_hybrid/nbest_predictions.json',
    '/data/ephemeral/home/roberta/outputs/korquad_2e5_union/nbest_predictions.json'
]


#  모든 JSON 파일 로드
loaded_data_list = []
for file_path in json_file_paths:
    try:
        with open(file_path, 'r', encoding='utf-8') as f:
            data = json.load(f)
            loaded_data_list.append(data)
    except FileNotFoundError:
        print(f"경고: 파일 '{file_path}'를 찾을 수 없습니다. 건너뜁니다.")
    except json.JSONDecodeError:
        print(f"오류: 파일 '{file_path}'의 JSON 형식이 올바르지 않습니다. 건너뜁니다.")


print(loaded_data_list)

# 앙상블 함수 실행
if loaded_data_list:
    ensemble_best_answers(loaded_data_list, 'union_ensemble_results.csv')
else:
    print("처리할 JSON 데이터가 없습니다.")

[{'mrc-1-000653': [{'start_logit': 3.4026999473571777, 'end_logit': 3.5971996784210205, 'text': '사락사라', 'probability': 0.9961069226264954}, {'start_logit': -2.866427421569824, 'end_logit': 3.5971996784210205, 'text': '40억년전 지구에서, 사락사라', 'probability': 0.0018865065649151802}, {'start_logit': -4.009252071380615, 'end_logit': 3.5971996784210205, 'text': '지구에서, 사락사라', 'probability': 0.0006016392144374549}, {'start_logit': -4.054358959197998, 'end_logit': 3.5971996784210205, 'text': '라', 'probability': 0.0005751040298491716}, {'start_logit': 3.4026999473571777, 'end_logit': -4.619110584259033, 'text': '사', 'probability': 0.0002691582194529474}, {'start_logit': -5.415775299072266, 'end_logit': 3.5971996784210205, 'text': '락사라', 'probability': 0.00014739767357241362}, {'start_logit': 3.4026999473571777, 'end_logit': -5.647420883178711, 'text': '사락사라의', 'probability': 9.625381062505767e-05}, {'start_logit': 3.4026999473571777, 'end_logit': -5.761762619018555, 'text': '사락사', 'probability': 8.58